In [1]:
import json
import numpy as np

from pathlib import Path

from tabulate import tabulate

In [2]:
benchmark_result_files = list(Path("./").rglob("*scandeval_benchmark_results.jsonl"))

print(benchmark_result_files)

model_id_results_mapping = {}

for benchmark_result_file in benchmark_result_files:                      
    model_id = None

    dataset_metrics_mapping = {}

    scores = []
    
    with open(benchmark_result_file) as f_p:
        for line in f_p:
            line = line.strip()
            if not line:
                continue
            data = json.loads(line)

            model_id = data["model"]
            dataset = data["dataset"]
            total = data["results"]["total"]
            if dataset == "conll-en":
                test_micro_f1_no_misc = round(total["test_micro_f1_no_misc"], 2)
                test_micro_f1_no_misc_se = round(total["test_micro_f1_no_misc_se"], 2)
                test_micro_f1 = round(total["test_micro_f1"], 2)
                test_micro_f1_se = round(total["test_micro_f1_se"], 2)

                scores.append(test_micro_f1_no_misc)
                scores.append(test_micro_f1)
                
                metric_string = f"{test_micro_f1_no_misc} ± {test_micro_f1_no_misc_se} / {test_micro_f1} ± {test_micro_f1_se}"
                dataset_metrics_mapping[dataset] = metric_string
            elif dataset in ["sst5", "scala-en"]:
                test_mcc = round(total["test_mcc"], 2)
                test_mcc_se = round(total["test_mcc_se"], 2)
                test_macro_f1 = round(total["test_macro_f1"], 2)
                test_macro_f1_se = round(total["test_macro_f1_se"], 2)

                scores.append(test_mcc)
                scores.append(test_macro_f1)
                
                metric_string = f"{test_mcc} ± {test_mcc_se} / {test_macro_f1} ± {test_macro_f1_se}"
                dataset_metrics_mapping[dataset] = metric_string
            elif dataset == "squad":
                test_em = round(total["test_em"], 2)
                test_em_se = round(total["test_em_se"], 2)
                test_f1 = round(total["test_f1"], 2)
                test_f1_se = round(total["test_f1_se"], 2)

                scores.append(test_em)
                scores.append(test_f1)
                
                metric_string = f"{test_em} ± {test_em_se} / {test_f1} ± {test_f1_se}"
                dataset_metrics_mapping[dataset] = metric_string

    score = round(np.mean(scores), 2)
    score_string = f"{score}"
    
    dataset_metrics_mapping["score"] = score_string
    
    print(model_id)
    
    model_id_results_mapping[model_id] = dataset_metrics_mapping

[PosixPath('electra-base/scandeval_benchmark_results.jsonl'), PosixPath('roberta-base/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-token-dropping-finewebs-1m/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-token-dropping-finewebs-801k/scandeval_benchmark_results.jsonl'), PosixPath('teams-base-finewebs-901k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-token-dropping-finewebs-851k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-finewebs-851k/scandeval_benchmark_results.jsonl'), PosixPath('teams-base-finewebs-951k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-finewebs-801k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-finewebs-901k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-cased/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-token-dropping-finewebs-901k/scandeval_benchmark_results.jsonl'), PosixPath('bert-base-finewebs-1m/scandeval_benchmark_results.jsonl'), PosixPath('teams-base-finewebs-851k

# Overall

In [3]:
model_id_order = [
    "model-garden-lms/bert-base-finewebs-1m",
    "model-garden-lms/bert-base-finewebs-951k",
    "model-garden-lms/bert-base-finewebs-901k",
    "model-garden-lms/bert-base-finewebs-851k",
    "model-garden-lms/bert-base-finewebs-801k",
    "model-garden-lms/bert-base-token-dropping-finewebs-1m",
    "model-garden-lms/bert-base-token-dropping-finewebs-951k",
    "model-garden-lms/bert-base-token-dropping-finewebs-901k",
    "model-garden-lms/bert-base-token-dropping-finewebs-851k",
    "model-garden-lms/bert-base-token-dropping-finewebs-801k",
    "model-garden-lms/teams-base-finewebs-1m",
    "model-garden-lms/teams-base-finewebs-951k",
    "model-garden-lms/teams-base-finewebs-901k",
    "model-garden-lms/teams-base-finewebs-851k",
    "model-garden-lms/teams-base-finewebs-801k",
    "google-bert/bert-base-cased",
    "google/electra-base-discriminator",
    "FacebookAI/roberta-base",
]

dataset_order = ["score", "conll-en", "sst5", "scala-en", "squad"]

In [4]:
headers = ["Model ID", "Avg. Score", "CoNLL-En", "SST5", "ScaLA-En", "SQuAD"]

table = []

for model_id in model_id_order:
    current_row = []
    
    model_id_markdown = f"[{model_id}](https://huggingface.co/{model_id})"
    current_row.append(model_id_markdown)

    for dataset in dataset_order:
        current_row.append(model_id_results_mapping[model_id][dataset])

    table.append(current_row)

In [5]:
print(tabulate(table, headers=headers, tablefmt="github"))

| Model ID                                                                                                                                  |   Avg. Score | CoNLL-En                    | SST5                        | ScaLA-En                    | SQuAD                       |
|-------------------------------------------------------------------------------------------------------------------------------------------|--------------|-----------------------------|-----------------------------|-----------------------------|-----------------------------|
| [model-garden-lms/bert-base-finewebs-1m](https://huggingface.co/model-garden-lms/bert-base-finewebs-1m)                                   |        69.03 | 88.98 ± 0.43 / 88.67 ± 0.36 | 58.11 ± 1.2 / 59.77 ± 1.49  | 57.29 ± 3.57 / 77.15 ± 2.17 | 55.82 ± 1.35 / 66.46 ± 1.51 |
| [model-garden-lms/bert-base-finewebs-951k](https://huggingface.co/model-garden-lms/bert-base-finewebs-951k)                               |        69.41 | 89.25 ± 0.4 